# Train a tree based model for regression task: predict delay difference

In [2]:
import datetime
import matplotlib.pyplot as plt
from matplotlib import pyplot
import pandas as pd
import sklearn
from sklearn.inspection import PartialDependenceDisplay
# from sklearn.neural_network import MLPRegressor
from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import StandardScaler
# from sklearn.tree import DecisionTreeRegressor
import numpy as np

pd.set_option("display.max_colwidth", 0)
pd.set_option("display.max_rows", 500)
pd.set_option("display.max_columns", 500)
pd.set_option("display.width", 1000)
import warnings
warnings.filterwarnings("ignore")
pd.options.display.float_format = '{:.5f}'.format

In [5]:
import sys
import logging
import datetime

nblog = open("./output/logs/tree_pdp_shap_"+str(datetime.datetime.now())+".log", "a+")
sys.stdout.echo = nblog
sys.stderr.echo = nblog

get_ipython().log.handlers[0].stream = nblog
get_ipython().log.setLevel(logging.INFO)

%autosave 5

Autosaving every 5 seconds


In [6]:
%%time

df_traffic = pd.read_csv('./output/austin_2022_GP_10min_interval_delaydifference_with_features_forML.csv')
df_traffic['minutes_since_midnight'] = df_traffic['hour_min'].apply(lambda x: int(x[:2]) * 60 + int(x[3:]))

print(df_traffic.date.unique())
print('unique road segments (samples):',df_traffic.tmc_code.unique().shape[0])
print('total observations: ',df_traffic.shape[0])
df_traffic.head(2)

['2022-10-21' '2022-10-22' '2022-10-23']
unique road segments (samples): 4450
total observations:  1917950
CPU times: user 3.69 s, sys: 285 ms, total: 3.97 s
Wall time: 3.97 s


tmc_code hour_min  delay_baseline  delay_focus  delay_difference        date                 intersection  start_latitude  start_longitude  end_latitude  end_longitude   miles  airbnb_count  distance_to_Shuttle_Waterloo_Park  distance_to_Shuttle_Barton_Creek_Square  distance_to_Shuttle_Expo_Center  distance_to_Uber_DelValle_HighSchool  distance_to_venue  minutes_since_midnight
0  112+04758  00:00   -0.93268        -0.93268     0.00000            2022-10-21  51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         0                     
1  112+04758  00:10   -0.93268        -0.93268     0.00000            2022-10-21  51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         10

In [7]:
# because the event usually begins in the morning after 10, people arrive typically around that time, so we want to only focus on after 930
df_traffic = df_traffic[df_traffic['minutes_since_midnight']>=540]
print(df_traffic.shape[0])
df_traffic = pd.get_dummies(df_traffic, columns=['date'], prefix='date')

1197050


In [8]:
df_traffic.columns

Index(['tmc_code', 'hour_min', 'delay_baseline', 'delay_focus', 'delay_difference', 'intersection', 'start_latitude', 'start_longitude', 'end_latitude', 'end_longitude', 'miles', 'airbnb_count', 'distance_to_Shuttle_Waterloo_Park', 'distance_to_Shuttle_Barton_Creek_Square', 'distance_to_Shuttle_Expo_Center', 'distance_to_Uber_DelValle_HighSchool', 'distance_to_venue', 'minutes_since_midnight', 'date_2022-10-21', 'date_2022-10-22', 'date_2022-10-23'], dtype='object')

In [9]:
# df_traffic_oneday = df_traffic[df_traffic['date']=='2022-10-22']

In [167]:
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error

# Prepare input features and labels for the model
X = df_traffic[['minutes_since_midnight',  'start_latitude', 'start_longitude', 'miles',
                'date_2022-10-21', 'date_2022-10-22', 'date_2022-10-23',
                'airbnb_count', 'distance_to_Shuttle_Waterloo_Park', 'distance_to_Shuttle_Barton_Creek_Square', 
                'distance_to_Shuttle_Expo_Center', 'distance_to_venue']].copy()
y = df_traffic['delay_difference'].values

# Split data into training and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42)

print('Total sample size:', X.shape[0])
print('Total training set size:', X_train.shape[0])
print('Total test set size:', X_test.shape[0])

Total sample size: 1197050
Total training set size: 837935
Total test set size: 359115


In [192]:
%%time
# check VIF
df_cor = X.corr()
pd.DataFrame(np.linalg.inv(X.corr().values), index = df_cor.index, columns=df_cor.columns)

CPU times: user 672 ms, sys: 47 ms, total: 719 ms
Wall time: 714 ms


minutes_since_midnight  start_latitude  start_longitude    miles       date_2022-10-21       date_2022-10-22       date_2022-10-23  airbnb_count  distance_to_Shuttle_Waterloo_Park  distance_to_Shuttle_Barton_Creek_Square  distance_to_Shuttle_Expo_Center  distance_to_venue
minutes_since_midnight                  1.00002                 0.00000         0.00000          0.00000  -0.00707              -0.00706              -0.01203              0.00000       0.00000                            -0.00000                                 -0.00000                         -0.00000          
start_latitude                          0.00000                 14.56469        -1.44345         0.62870  -0.06620              -0.06620              -0.06602              0.17140       3.76433                            -1.60359                                 5.80307                          -17.94655         
start_longitude                         0.00000                 -1.44345        4.66875          0.19144  0.03619               0.03619               0.03609               -0.41848      -0.21420                           -6.39994                                 2.55270                          3.84068           
miles                                   0.00000                 0.62870         0.19144          1.24380  0.10307               0.10307               0.10278               -0.14788      -0.92821                           -0.11492                                 0.45082                          -0.28031          
date_2022-10-21                         -0.00706                -0.06620        0.03619          0.10307  -22866999849187.30078 -22866999849188.27734 -22803036087951.56250 0.04121       -0.01758                           -0.03943                                 0.01912                          0.07762           
date_2022-10-22                         -0.00706                -0.06620        0.03619          0.10307  -22866999849188.27734 -22866999849187.92578 -22803036087951.87500 0.04121       -0.01758                           -0.03943                                 0.01912                          0.07762           
date_2022-10-23                         -0.01202                -0.06602        0.03609          0.10278  -22803036087951.56250 -22803036087951.87500 -22739251246676.81641 0.04110       -0.01753                           -0.03932                                 0.01907                          0.07741           
airbnb_count                            0.00000                 0.17140         -0.41848         -0.14788 0.04121               0.04121               0.04110               1.70574       6.01917                            -3.11416                                 -2.28398                         -0.34679          
distance_to_Shuttle_Waterloo_Park       0.00000                 3.76433         -0.21420         -0.92821 -0.01758              -0.01758              -0.01753              6.01917       73.73619                           -49.67775                                -25.68463                        -3.63288          
distance_to_Shuttle_Barton_Creek_Square -0.00000                -1.60359        -6.39994         -0.11492 -0.03943              -0.03943              -0.03932              -3.11416      -49.67775                          45.89182                                 12.69935                         -3.61961          
distance_to_Shuttle_Expo_Center         -0.00000                5.80307         2.55270          0.45082  0.01912               0.01912               0.01907               -2.28398      -25.68463                          12.69935                                 16.82524                         -6.95428          
distance_to_venue                       -0.00000                -17.94655       3.84068          -0.28031 0.07762               0.07762               0.07741               -0.34679      -3.63288                           -3.61961                                 -6.95428   

# Hyperparameter tuning using optuna

In [207]:
# %%time
# # %pip install optuna
# ## this step took 10 hours to finish

# import optuna
# from sklearn.model_selection import cross_val_score, KFold
# from sklearn.metrics import make_scorer, mean_squared_error

# def objective(trial):
#     # Define hyperparameters to optimize
#     params = {
#         "objective": "regression",
#         "metric": "rmse",
#         "num_leaves": trial.suggest_int("num_leaves", 20, 150),
#         "max_depth": trial.suggest_int("max_depth", 3, 15),
#         "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
#         "n_estimators": trial.suggest_int("n_estimators", 100, 1000),
#         "min_child_samples": trial.suggest_int("min_child_samples", 10, 100),
#         "min_child_weight": trial.suggest_float("min_child_weight", 1e-3, 1e-1, log=True),
#         "lambda_l1": trial.suggest_float("lambda_l1", 0.0, 10.0),
#         "lambda_l2": trial.suggest_float("lambda_l2", 0.0, 10.0),
#         "feature_fraction": trial.suggest_float("feature_fraction", 0.6, 1.0),
#         "bagging_fraction": trial.suggest_float("bagging_fraction", 0.6, 1.0),
#         "bagging_freq": trial.suggest_int("bagging_freq", 1, 10),
#     }
    
    
#     # Initialize CatBoostRegressor with the suggested hyperparameters
#     model = LGBMRegressor(**params)
    
#     # Perform cross-validation
#     kf = KFold(n_splits=5, shuffle=True, random_state=42)
# #     kf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    
#     rmse_scorer = make_scorer(mean_squared_error, squared=False)
#     scores = cross_val_score(model, X_train, y_train, cv=kf, scoring=rmse_scorer)

#     return scores.mean()

# # Create a study and optimize the objective function
# study = optuna.create_study(direction='minimize')
# study.optimize(objective, n_trials=50)

In [205]:
# Output the best hyperparameters
print('Best trial:', study.best_trial.params)
print('Best RMSE:', study.best_trial.value)

Best trial: {'num_leaves': 87, 'max_depth': 15, 'learning_rate': 0.14792701661878016, 'n_estimators': 703, 'min_child_samples': 11, 'min_child_weight': 0.028726468169652887, 'lambda_l1': 5.2390618151082915, 'lambda_l2': 6.658775197324868, 'feature_fraction': 0.8797006144268615, 'bagging_fraction': 0.8541212309086978, 'bagging_freq': 10}
Best RMSE: 13.352665446652873


# Training: LightGBM
https://lightgbm.readthedocs.io/en/latest/index.html

In [169]:
# import lightgbm as lgb
from lightgbm import LGBMRegressor

# Create LightGBM dataset
train_data = lgb.Dataset(X_train, label=y_train)
test_data = lgb.Dataset(X_test, label=y_test, reference=train_data)

In [ ]:
%%time
params = study.best_trial.params
model = LGBMRegressor(**params)
model.fit(X_train, y_train)

In [ ]:
import joblib

output_path = './output/lightgbm_model_' + str(datetime.datetime.now()) + '.pkl'
joblib.dump(model, output_path)

# Model evaluation

In [55]:
%%time 
import lightgbm as lgb

# Load the model back

output_path = './output/lightgbm_model_2024-11-18 17:08:58.212481.pkl'
model = joblib.load(output_path)
print("Model loaded successfully!")

Model loaded successfully!
CPU times: user 26.4 ms, sys: 20 ms, total: 46.4 ms
Wall time: 4.83 ms


In [206]:
%%time

import numpy as np
from sklearn.metrics import mean_squared_log_error
from sklearn.metrics import mean_squared_error, r2_score

y_pred = model.predict(X_test)

mse = mean_squared_error(y_test, y_pred)
rmse = np.sqrt(mse)
print(datetime.datetime.now(),'Best Model RMSE: %.3f' % rmse)

r2 = r2_score(y_test, y_pred)
print(datetime.datetime.now(),'Best Model R-squared: %.3f' % r2)

2024-11-19 20:09:33.588097 Best Model RMSE: 13.741
2024-11-19 20:09:33.590961 Best Model R-squared: 0.540
CPU times: user 12.2 s, sys: 210 ms, total: 12.4 s
Wall time: 916 ms


# PDP

In [ ]:
feature_list_continuous= ['minutes_since_midnight','airbnb_count',
                          'distance_to_Shuttle_Waterloo_Park', 'distance_to_Shuttle_Barton_Creek_Square', 
                          'distance_to_Shuttle_Expo_Center',  'distance_to_venue'
                          ]
print('number of continuous features:',len(feature_list_continuous))
# feature_list_cat = []

In [ ]:
%%time 
from sklearn.inspection import PartialDependenceDisplay
# ~5min per PDP graph
# using for loop, otherwise might occur memory errors
# PDP for continuous features and save the graph for each feature separately
print(datetime.datetime.now(),'*************** Start running PDP: feature_list_continuous ***************')

for feature_one in feature_list_continuous:
    print(datetime.datetime.now(), feature_one)
    plt.rcParams.update({'font.size': 14})
    fig, ax = plt.subplots(figsize=(5,5))
    pdp_one = PartialDependenceDisplay.from_estimator(model, X, [feature_one],n_jobs = 6, ax=ax)
    plt.savefig('./output/pdp_' + feature_one + '.pdf', bbox_inches="tight")

print(datetime.datetime.now(),'*************** Done running PDP: feature_list_continuous ***************')

# SHAP

In [ ]:
%%time
# 4min 25s
import shap

print(datetime.datetime.now(),'*************** Start running SHAP ***************')
explainer = shap.TreeExplainer(model)
shap_values = explainer(X) # this line takes very long

In [ ]:
%%time
# save shap values for each observation
# this takes 
shaplist = ['shap_'+i for i in X.columns]
df_shape_values = pd.DataFrame(shap_values.values, columns=shaplist)

df_shape_values['tmc_code'] = df_traffic['tmc_code'].values
df_shape_values['minutes_since_midnight'] = df_traffic['minutes_since_midnight'].values
df_shape_values['date_2022-10-21'] = df_traffic['date_2022-10-21'].values
df_shape_values['date_2022-10-22'] = df_traffic['date_2022-10-22'].values
df_shape_values['date_2022-10-23'] = df_traffic['date_2022-10-23'].values

first_column = df_shape_values.pop('tmc_code')
df_shape_values.insert(0, 'tmc_code', first_column)

df_shape_values.to_csv('./output/shap_values.csv',sep=',',index=False)
df_shape_values.head()

In [ ]:
print(df_traffic.shape[0])
print(df_shape_values.shape[0])

In [ ]:
%%time
print(datetime.datetime.now(),'*************** Start running SHAP importance ***************')
plt.rcParams.update({'font.size': 16})
fig, ax = plt.subplots(1,1,figsize=(6,6))
shap_importance = shap_values.abs.mean(0).values
sorted_idx = shap_importance.argsort()
plt.barh(range(len(sorted_idx)), shap_importance[sorted_idx], align='center',color="#4c72b0") #'turquoise'
plt.yticks(range(len(sorted_idx)), np.array(X.columns)[sorted_idx])
plt.xlabel('SHAP Importance')
plt.savefig('./output/feature_importance_shap.pdf', bbox_inches='tight')

In [ ]:
# %%time
# # ~6min
# # Reading about gray colors: https://mlconference.ai/blog/tutorial-explainable-machine-learning-with-python-and-shap/
# print(datetime.datetime.now(),'*************** Start running beeswarm ***************')
# fig_beeswarm = shap.plots.beeswarm(shap_values,show=False, max_display=50)
# plt.savefig('./output/shap_beeswarm.pdf', bbox_inches='tight')

# Spatial SHAP

In [208]:
df_shap_merged = df_traffic.merge(df_shape_values, ) #on=['tmc_code', 'minutes_since_midnight', 'date_2022-10-21','date_2022-10-22','date_2022-10-23']
print(df_shap_merged.shape[0])
df_shap_merged.head()

1197050


tmc_code hour_min  delay_baseline  delay_focus  delay_difference                 intersection  start_latitude  start_longitude  end_latitude  end_longitude   miles  airbnb_count  distance_to_Shuttle_Waterloo_Park  distance_to_Shuttle_Barton_Creek_Square  distance_to_Shuttle_Expo_Center  distance_to_Uber_DelValle_HighSchool  distance_to_venue  minutes_since_midnight  date_2022-10-21  date_2022-10-22  date_2022-10-23  shap_minutes_since_midnight  shap_start_latitude  shap_start_longitude  shap_miles  shap_date_2022-10-21  shap_date_2022-10-22  shap_date_2022-10-23  shap_airbnb_count  shap_distance_to_Shuttle_Waterloo_Park  shap_distance_to_Shuttle_Barton_Creek_Square  shap_distance_to_Shuttle_Expo_Center  shap_distance_to_venue
0  112+04758  09:00   -0.93268        -0.93268     0.00000            51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         540                     1                0                0               0.56965                      -0.22642             0.27543               -0.47553    0.87596               0.37087               0.00708               0.49758            -1.45214                                0.36641                                       0.51925                               -0.39943               
1  112+04758  09:10   -0.93268        -0.93268     0.00000            51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         550                     1                0                0               0.36039                      -0.24958             0.20372               -0.41456    0.72467               0.36803               0.00550               0.51247            -1.48833                                0.48790                                       0.53739                               -0.37360               
2  112+04758  09:20   -0.93268        -0.93268     0.00000            51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         560                     1                0                0               0.48165                      -0.24011             0.17320               -0.43313    0.72036               0.38152               0.00622               0.53013            -1.49590                                0.49446                                       0.56756                               -0.38635               
3  112+04758  09:30   -0.33268        -0.93268     -0.60000           51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763                           23552.59734         570                     1                0                0               0.17636                      -0.30493             0.11909               -0.42372    0.57614               0.38593               -0.00106              0.46805            -1.63182                                0.58504                                       0.56580                               -0.40954               
4  112+04758  09:40   -0.33268        -0.93268     -0.60000           51ST ST/CAMERON RD/EXIT 237 30.30330        -97.71418        30.30530      -97.71289      0.15814  87           4685.01085                         11838.72611                              10171.97090                      19603.37763  

In [209]:
print('average prediction:', df_shap_merged.shap_minutes_since_midnight.mean())

average prediction: 0.010008220680972967


In [210]:
# Create a polygon for event venue
from shapely.geometry import Polygon
import geopandas as gpd

lat_point_list = [30.131962, 30.146337, 30.140386, 30.122629]
lon_point_list = [-97.647388, -97.635686, -97.619652, -97.631465]
polygon_geom = Polygon(zip(lon_point_list, lat_point_list))
polygon = gpd.GeoDataFrame(index=[0], crs='epsg:4326', geometry=[polygon_geom])       
polygon['name']  = 'the Circuit of the Americas'
polygon
# polygon.explore()

import shapely.geometry as geom

# Create Shapely point geometries
point_waterloo_park = geom.Point(-97.736285, 30.273726) # (longitude, latitude)
point_barton_creek_square = geom.Point(-97.805046, 30.257509)
point_expo_center = geom.Point(-97.622544, 30.297062)
point_ridehailing = geom.Point(-97.614135, 30.178718)

point_shuttle_list = [point_waterloo_park,point_barton_creek_square,point_expo_center,point_ridehailing]
gdf_shuttle = gpd.GeoDataFrame({'Shuttle_Location': ['Shuttle_Waterloo_Park', 'Shuttle_Barton_Creek_Square', 'Shuttle_Expo_Center', 'Uber_DelValle_HighSchool'],
                        'geometry': point_shuttle_list},
                        crs="EPSG:4326")
# gdf_shuttle

In [211]:
df_road = pd.read_csv("data/TMC_Identification.csv", sep=',', header=0)
df_road = df_road[['tmc_code','intersection','start_latitude','start_longitude','end_latitude','end_longitude','miles']]

from shapely.geometry import LineString
from geopandas import GeoDataFrame

df_road['geometry'] = df_road.apply(
    lambda row: LineString([(row['start_longitude'], row['start_latitude']),
                             (row['end_longitude'], row['end_latitude'])]),
    axis=1
)

# Create a GeoDataFrame
gdf_road = GeoDataFrame(df_road, geometry='geometry',crs="EPSG:4326")
print(gdf_road.shape[0])

4460


In [216]:
# Select one time point and plot the SHAP values of several features at that specfic time point
hourmin_select, date_select = 600, 'date_2022-10-22'
df_plotshap = df_shap_merged[(df_shap_merged['minutes_since_midnight'] == hourmin_select)&(df_shap_merged[date_select] == 1)]
df_plotshap['shap_coordinates'] = df_plotshap['shap_start_latitude'] + df_plotshap['shap_start_longitude']
print(df_plotshap.shape[0])
print(gdf_road.shape[0])

gdf_road_merged = gdf_road.merge(df_plotshap,) #left_on='tmc', right_on='tmc_code'
print(gdf_road_merged.shape[0])
gdf_road_merged.shap_coordinates.describe()

4450
4460
4291


count   4291.00000
mean    -0.37063  
std     1.52519   
min     -36.18779 
25%     -0.89014  
50%     -0.19453  
75%     0.20923   
max     18.91092  
Name: shap_coordinates, dtype: float64

In [217]:
gdf_road_merged.columns

Index(['tmc_code', 'intersection', 'start_latitude', 'start_longitude', 'end_latitude', 'end_longitude', 'miles', 'geometry', 'hour_min', 'delay_baseline', 'delay_focus', 'delay_difference', 'airbnb_count', 'distance_to_Shuttle_Waterloo_Park', 'distance_to_Shuttle_Barton_Creek_Square', 'distance_to_Shuttle_Expo_Center', 'distance_to_Uber_DelValle_HighSchool', 'distance_to_venue', 'minutes_since_midnight', 'date_2022-10-21', 'date_2022-10-22', 'date_2022-10-23', 'shap_minutes_since_midnight', 'shap_start_latitude', 'shap_start_longitude', 'shap_miles', 'shap_date_2022-10-21', 'shap_date_2022-10-22', 'shap_date_2022-10-23', 'shap_airbnb_count', 'shap_distance_to_Shuttle_Waterloo_Park', 'shap_distance_to_Shuttle_Barton_Creek_Square', 'shap_distance_to_Shuttle_Expo_Center', 'shap_distance_to_venue', 'shap_coordinates'], dtype='object')

In [219]:
%%time
# congestion_colors = ["#00FF00", "#ADFF2F", "#FFFF00", "#FFA500", "#FF0000", "#8B0000"]
print('date:', date_select)
print('hour',hourmin_select/60)
m = gdf_road_merged.explore(
    column='shap_distance_to_venue',
    cmap= 'rainbow',
    tiles="CartoDB Positron", # OpenStreetMap, CartoDB dark_matter, CartoDB Positron
    categorical=False
)

m = gdf_shuttle.explore(
    m=m,
    markersize=40,
    linewidth=2,
    edgecolor="black",
)

polygon.explore(
    m=m
)

date: date_2022-10-22
hour 10.0
CPU times: user 788 ms, sys: 183 ms, total: 971 ms
Wall time: 18.9 s
